## Erste Analyse der MedReg Daten über Psychiater
In diesem Notebook sollen die bereigten Daten aus dem Notenook [MedReg_Analyse_01_Bereinigen](MedReg_Analyse_01_Bereinigen.ipynb) einer ersten Analyse unterzogen werden. 
Im Hinblick auf den Beitrag in der «PULS»-Sendung vom 17.2.2020 sollen die im [csv-File]( http://localhost:8888/edit/Desktop/CAS_DJ/MedReg/MedReg%20Scraping%202020/medreg_2020_psych_20200121.csv) abgelegten «dreckigen» Daten zuerst folgenden, (hoffentlich) einfacheren Analysen unterzogen werden:

1. Stand der Facharztabschlüsse und Nationalität per Ende 2019 (auf Basis von Land Medizinsudium und der direkten Anerkennungen ausländischer Facharzttiteln
2. Aussagen über die Nationalität bzw. Studienort der anerkannten Weiterbildungstitel
4. Anteil aller Psychiater mit ausländischer Herkunft per Ende 2019


In weiteren Analysen sollen später auch Fragen untersucht werden, wie:

5. Entwicklung Gesamtanteil über die Jahre, bis Ende 2019
6. Entwicklung Anteil der Anerkennung (sprich: Neuzulassung) per Jahresende, über die Jahre, bis Ende 2019
7. regionale Aussagen über die Tätigkeitsorte (Adresse der Bewilligung) wie zum Beispiel:
  - Vergleich zur Kantonsbevölkerung? (aussagekräftig?)
  - Städtische Gebiete, ländliche Gebiete? (aufwändig)
  - Grossstädte vs. landliche Zentren?

In [1]:
import pandas as pd
import re
import numpy as np
import datetime

In [67]:
df = pd.read_csv('medreg_2020_psych_20200125.csv')

In [68]:
df.head(3)

Unnamed: 0  Doc_ID                 Name Geschlecht  \
0           0     552   Poleski, Alexander          m   
1           1     566   Langegger, Florian          m   
2           2     590  Rivera Prada, Jaime          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   

        Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  PP_Jahr  PP_Land  \
0   Französisch       1985   Schweiz                    NaN     1986  Schweiz   
1       Deutsch       1985   Schweiz                    NaN     1985  Schweiz   
2   Französisch       1985   Schweiz                    NaN     1987  Schweiz   

   PP_Anerkennung                                                BAB  \
0             NaN  Waadt                (1986), aktiv, MedBG, pri...   
1             NaN  Thurgau                (2017), aktiv, MedBG, p...   
2             NaN   Wallis                (2014), inaktiv, Unbekannt   

  BAB Status            Datei  
0    Erteilt  medreg_552.html  
1    Erteilt  medreg_566.html  
2    Erteilt  medreg_590.html

Zuerst interessiert uns aber noch die Frage, wieviele in der Datenbank im Jahr 2020 bereits aufgenommen wurden. Da wir nur die Daten bis Ende 2019 auswerten wollen, müssen wir diese Personen in einem zweiten Schritt ausschliessen. 


In [41]:
df[df['PP_Anerkennung'] == 2020]

Unnamed: 0  Doc_ID                              Name Geschlecht  \
4699        4699   81218       Olszewski, Konrad Stanislaw          m   
5232        5232   98760        Kostov, Christian Stoyanov          m   
5399        5399  109949             Lupu, Madalina-Carmen          w   
5433        5433  113811             Noller, Silvia-Corina          w   
5434        5434  113880            Fehr, Monika Hildegard          w   
5435        5435  113887        Schneider, Hannah Adelheid          w   
5436        5436  113984  Alexanian, Jean-Baptiste Hemayak          m   

                                      Adresse                 Ort  \
4699                             Kein Eintrag                 NaN   
5232  Seeblickstrasse 3,8596 Münsterlingen,TG  8596 Münsterlingen   
5399                             Kein Eintrag                 NaN   
5433                             Kein Eintrag                 NaN   
5434                             Kein Eintrag                 NaN   
5435                             Kein Eintrag                 NaN   
5436                             Kein Eintrag                 NaN   

           Nationalität                Sprache  Arzt_Jahr    Arzt_Land  \
4699   Deutschland (DE)                Deutsch       2013  Deutschland   
5232     Bulgarien (BG)                Deutsch       1995    Bulgarien   
5399      Rumänien (RO)                              2006     Rumänien   
5433   Deutschland (DE)   Deutsch, Französisch       1985     Rumänien   
5434   Deutschland (DE)                Deutsch       1987  Deutschland   
5435   Deutschland (DE)                Deutsch       2013  Deutschland   
5436    Frankreich (FR)            Französisch       2013   Frankreich   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
4699                 2013.0     2019  Deutschland          2020.0   
5232                 2017.0     2011  Deutschland          2020.0   
5399                 2019.0     2012     Rumänien          2020.0   
5433                 2020.0     2001  Deutschland          2020.0   
5434                 2020.0     1995  Deutschland          2020.0   
5435                 2020.0     2019  Deutschland          2020.0   
5436                 2020.0     2013   Frankreich          2020.0   

                                                    BAB    BAB Status  \
4699                                       Kein Eintrag  Kein Eintrag   
5232  Thurgau                (2017), aktiv, Kt. Rech...       Erteilt   
5399                                       Kein Eintrag  Kein Eintrag   
5433                                       Kein Eintrag  Kein Eintrag   
5434                                       Kein Eintrag  Kein Eintrag   
5435                                       Kein Eintrag  Kein Eintrag   
5436                                       Kein Eintrag  Kein Eintrag   

                   Datei  
4699   medreg_81218.html  
5232   medreg_98760.html  
5399  medreg_109949.html  
5433  medreg_113811.html  
5434  medreg_113880.html  
5435  medreg_113887.html  
5436  medreg_113984.html

Es sind also 3 Psychiater und 4 Psychiater, deren Titel 2020 bereits bis Mitte Januar anerkannt worden sind. 
Wir schliessen diese Daten aus:

In [69]:
df = df[~(df['PP_Anerkennung'] == 2020)]

In [70]:
len(df)

5430

In [71]:
df.head(3)

Unnamed: 0  Doc_ID                 Name Geschlecht  \
0           0     552   Poleski, Alexander          m   
1           1     566   Langegger, Florian          m   
2           2     590  Rivera Prada, Jaime          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   

        Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  PP_Jahr  PP_Land  \
0   Französisch       1985   Schweiz                    NaN     1986  Schweiz   
1       Deutsch       1985   Schweiz                    NaN     1985  Schweiz   
2   Französisch       1985   Schweiz                    NaN     1987  Schweiz   

   PP_Anerkennung                                                BAB  \
0             NaN  Waadt                (1986), aktiv, MedBG, pri...   
1             NaN  Thurgau                (2017), aktiv, MedBG, p...   
2             NaN   Wallis                (2014), inaktiv, Unbekannt   

  BAB Status            Datei  
0    Erteilt  medreg_552.html  
1    Erteilt  medreg_566.html  
2    Erteilt  medreg_590.html

In [72]:
df.to_csv(r'medreg_2020_psych_b2019_20200126.csv',index = True, header=True)

### 1. Stand der Facharztabschlüsse und Nationalität per Ende 2019
Bereits für diese Fragestellung können wir mit den vorhandenen Daten mehrere Antworten liefern. 
Zum Beispiel: welche Staatsbürgerschaft haben die eingetragenen Psychiaterinnen und Psychiater? In welchem Land haben Sie ihr Medizin-Grundstudium absolviert?

Wir untersuchen die Daten zuerst bezüglich Nationalität:

In [59]:
df_nat = df['Nationalität'].value_counts()

In [61]:
df_nat = df_nat.reset_index()

In [62]:
df_nat = df_nat.rename(columns = {'index':'Nation', 'Nationalität':'Anzahl'})
df_nat

Nation  Anzahl
0                           Schweiz (CH)    2943
1                       Deutschland (DE)    1365
2                        Frankreich (FR)     356
3                           Italien (IT)     189
4                        Österreich (AT)     163
5                      Griechenland (GR)      73
6                           Spanien (ES)      66
7                          Rumänien (RO)      44
8                           Belgien (BE)      35
9                       Niederlande (NL)      15
10                        Bulgarien (BG)      15
11                            Polen (PL)      12
12                           Ungarn (HU)      11
13                         Portugal (PT)      11
14                  Grossbritannien (GB)       8
15                         Tunesien (TN)       7
16                 Serbien Republik (RS)       6
17                         Kroatien (HR)       6
18                         Finnland (FI)       5
19                         Algerien (DZ)       5
20                         Slowakei (SK)       5
21                        Slowenien (SI)       5
22                         Schweden (SE)       5
23                        Luxemburg (LU)       4
24             Russische Föderation (RU)       4
25                             Iran (IR)       4
26     Demokratische Republik Kongo (CD)       3
27                          Kamerun (CM)       3
28                             Kuba (CU)       3
29                           Ruanda (RW)       3
30                         Norwegen (NO)       3
31                           Türkei (TR)       2
32                      Jugoslawien (YU)       2
33            Tschechische Republik (CZ)       2
34                    Liechtenstein (LI)       2
35          Bosnien und Herzegowina (BA)       2
36   Vereinigte Staaten von Amerika (US)       2
37                       Mazedonien (MK)       2
38                           Zypern (CY)       2
39                          Marokko (MA)       2
40                          Ägypten (EG)       2
41                    Weissrussland (BY)       2
42                      Afghanistan (AF)       2
43                             Peru (PE)       2
44                        Venezuela (VE)       2
45                          Burundi (BI)       1
46                             Irak (IQ)       1
47                         Georgien (GE)       1
48           Serbien und Montenegro (CS)       1
49        Syrien arabische Republik (SY)       1
50                          Vietnam (VN)       1
51                       Madagaskar (MG)       1
52                           Canada (CA)       1
53                            China (CN)       1
54           vorm. Tschechoslowakei (CS)       1
55                        Palestina (PS)       1
56                        Guatemala (GT)       1
57                          Litauen (LT)       1
58                          Uruguay (UY)       1
59                         Armenien (AM)       1
60                        Kolumbien (CO)       1
61                          Estland (EE)       1
62                        Brasilien (BR)       1
63                           Kosovo (XK)       1
64                            Japan (JP)       1
65                            Chile (CL)       1
66                         Albanien (AL)       1
67                           Israel (IL)       1
68                         Lettland (LV)       1
69                          Ukraine (UA)       1

In [63]:
df_nat['Anteil'] = df_nat['Anzahl'] / 5430 * 100

In [64]:
df_nat

Nation  Anzahl     Anteil
0                           Schweiz (CH)    2943  54.198895
1                       Deutschland (DE)    1365  25.138122
2                        Frankreich (FR)     356   6.556169
3                           Italien (IT)     189   3.480663
4                        Österreich (AT)     163   3.001842
5                      Griechenland (GR)      73   1.344383
6                           Spanien (ES)      66   1.215470
7                          Rumänien (RO)      44   0.810313
8                           Belgien (BE)      35   0.644567
9                       Niederlande (NL)      15   0.276243
10                        Bulgarien (BG)      15   0.276243
11                            Polen (PL)      12   0.220994
12                           Ungarn (HU)      11   0.202578
13                         Portugal (PT)      11   0.202578
14                  Grossbritannien (GB)       8   0.147330
15                         Tunesien (TN)       7   0.128913
16                 Serbien Republik (RS)       6   0.110497
17                         Kroatien (HR)       6   0.110497
18                         Finnland (FI)       5   0.092081
19                         Algerien (DZ)       5   0.092081
20                         Slowakei (SK)       5   0.092081
21                        Slowenien (SI)       5   0.092081
22                         Schweden (SE)       5   0.092081
23                        Luxemburg (LU)       4   0.073665
24             Russische Föderation (RU)       4   0.073665
25                             Iran (IR)       4   0.073665
26     Demokratische Republik Kongo (CD)       3   0.055249
27                          Kamerun (CM)       3   0.055249
28                             Kuba (CU)       3   0.055249
29                           Ruanda (RW)       3   0.055249
30                         Norwegen (NO)       3   0.055249
31                           Türkei (TR)       2   0.036832
32                      Jugoslawien (YU)       2   0.036832
33            Tschechische Republik (CZ)       2   0.036832
34                    Liechtenstein (LI)       2   0.036832
35          Bosnien und Herzegowina (BA)       2   0.036832
36   Vereinigte Staaten von Amerika (US)       2   0.036832
37                       Mazedonien (MK)       2   0.036832
38                           Zypern (CY)       2   0.036832
39                          Marokko (MA)       2   0.036832
40                          Ägypten (EG)       2   0.036832
41                    Weissrussland (BY)       2   0.036832
42                      Afghanistan (AF)       2   0.036832
43                             Peru (PE)       2   0.036832
44                        Venezuela (VE)       2   0.036832
45                          Burundi (BI)       1   0.018416
46                             Irak (IQ)       1   0.018416
47                         Georgien (GE)       1   0.018416
48           Serbien und Montenegro (CS)       1   0.018416
49        Syrien arabische Republik (SY)       1   0.018416
50                          Vietnam (VN)       1   0.018416
51                       Madagaskar (MG)       1   0.018416
52                           Canada (CA)       1   0.018416
53                            China (CN)       1   0.018416
54           vorm. Tschechoslowakei (CS)       1   0.018416
55                        Palestina (PS)       1   0.018416
56                        Guatemala (GT)       1   0.018416
57                          Litauen (LT)       1   0.018416
58                          Uruguay (UY)       1   0.018416
59                         Armenien (AM)       1   0.018416
60                        Kolumbien (CO)       1   0.018416
61                          Estland (EE)       1   0.018416
62                        Brasilien (BR)       1   0.018416
63                           Kosovo (XK)       1   0.018416
64                            Japan (JP)       1   0.018416
65                            Chile (CL)       1   0.018416
66            

In [65]:
df_nat.to_csv(r'Psych_Nation_all_bis2019.csv',index = 'Nation', header=True)

### Resultat 1: Nationalität aller registrierten Psychiaterinnen und Psychiater
Erkenntnis: 54.2% aller registrierten Ärzte mit einem Weiterbildungstitel *Psychiaterie und Psychotherapie* sind Schweizer. Rund ein Viertel sind deutscher Nationalität. Weitere 10% sind Franzosen oder Italiener. Die Aussagekraft dieser Zahlen wird dadurch etwas eingeschränkt, da sich vermutlich viele Ärzte, die länger hier tätig sind, einbürgern lassen.

Im nächsten Schritt werten wir die Daten aller Einträge mit erteilter Berufsausübungsbewilligung (BAB) aus. Allerdings ist es denkbar, dass auch Ärzte ohne erteilte Berufsausübungsbewilligung in unselbstständiger Tätigkeit an Institutionen oder in delegierter Form tätig sind. In der Tendenz bildet die BAB wohl noch mehr die Tätigkeit als niedergelassener Arzt ab, auch wenn weder die Berufsausübungsbewilligung noch die Anerkennung des Diploms direkt aussagen, ob und in welchem Umfang die Tätigkeit als Psychiaterin, Psychiater auch tatsächlich ausgeübt werden. 

In [76]:
df = pd.read_csv('medreg_2020_psych_b2019_20200126.csv')

In [77]:
df_bab = df[df['BAB Status'] == 'Erteilt']

In [78]:
len(df_bab)

4427

Wir haben also 4427 Ärztinnen und Ärzte gefunden mit erteilter BAB (bis 31.12.2019)

In [80]:
df_bab_nat = df_bab['Nationalität'].value_counts()

In [81]:
df_bab_nat = df_bab_nat.reset_index()

In [83]:
df_bab_nat = df_bab_nat.rename(columns = {'index':'Nation', 'Nationalität':'Anzahl'})

In [84]:
df_bab_nat['Anteil'] = df_bab_nat['Anzahl'] / 4427 * 100

In [85]:
df_bab_nat

Nation  Anzahl     Anteil
0                           Schweiz (CH)    2646  59.769596
1                       Deutschland (DE)     979  22.114299
2                        Frankreich (FR)     228   5.150215
3                        Österreich (AT)     129   2.913937
4                           Italien (IT)     125   2.823583
5                      Griechenland (GR)      57   1.287554
6                           Spanien (ES)      50   1.129433
7                          Rumänien (RO)      35   0.790603
8                           Belgien (BE)      27   0.609894
9                          Portugal (PT)       8   0.180709
10                           Ungarn (HU)       8   0.180709
11                            Polen (PL)       8   0.180709
12                        Bulgarien (BG)       7   0.158121
13                      Niederlande (NL)       7   0.158121
14                         Tunesien (TN)       7   0.158121
15                         Kroatien (HR)       5   0.112943
16                        Slowenien (SI)       5   0.112943
17                  Grossbritannien (GB)       5   0.112943
18                         Finnland (FI)       4   0.090355
19                         Algerien (DZ)       4   0.090355
20                         Slowakei (SK)       4   0.090355
21                             Iran (IR)       4   0.090355
22                 Serbien Republik (RS)       4   0.090355
23                         Norwegen (NO)       3   0.067766
24             Russische Föderation (RU)       3   0.067766
25                             Kuba (CU)       3   0.067766
26                          Kamerun (CM)       3   0.067766
27     Demokratische Republik Kongo (CD)       3   0.067766
28                        Luxemburg (LU)       3   0.067766
29                         Schweden (SE)       3   0.067766
30                    Weissrussland (BY)       2   0.045177
31   Vereinigte Staaten von Amerika (US)       2   0.045177
32                           Ruanda (RW)       2   0.045177
33                           Zypern (CY)       2   0.045177
34                        Venezuela (VE)       2   0.045177
35                       Mazedonien (MK)       2   0.045177
36          Bosnien und Herzegowina (BA)       2   0.045177
37                      Jugoslawien (YU)       2   0.045177
38                             Peru (PE)       2   0.045177
39                          Ägypten (EG)       2   0.045177
40                          Marokko (MA)       2   0.045177
41            Tschechische Republik (CZ)       2   0.045177
42                           Türkei (TR)       2   0.045177
43                        Brasilien (BR)       1   0.022589
44                      Afghanistan (AF)       1   0.022589
45        Syrien arabische Republik (SY)       1   0.022589
46                            Chile (CL)       1   0.022589
47                        Palestina (PS)       1   0.022589
48                         Albanien (AL)       1   0.022589
49                           Israel (IL)       1   0.022589
50                            Japan (JP)       1   0.022589
51                            China (CN)       1   0.022589
52           vorm. Tschechoslowakei (CS)       1   0.022589
53                           Kosovo (XK)       1   0.022589
54                          Burundi (BI)       1   0.022589
55                         Georgien (GE)       1   0.022589
56                         Armenien (AM)       1   0.022589
57                          Vietnam (VN)       1   0.022589
58                          Uruguay (UY)       1   0.022589
59                          Ukraine (UA)       1   0.022589
60                          Estland (EE)       1   0.022589
61                        Kolumbien (CO)       1   0.022589
62                          Litauen (LT)       1   0.022589
63                       Madagaskar (MG)       1   0.022589
64                         Lettland (LV)       1   0.022589
65                           Canada (CA)       1   0.022589
66            

In [86]:
df_bab_nat.to_csv(r'Psych_Nation_bab_bis2019.csv',index = 'Nation', header=True)

#### Resultat 2: 60% mit erteilter Berufsbewilligung haben Schweizer Pass
Das Resultat: mit erteilter Berufsausübungsanteil steigt der Anteil an Schweizern auf 60%. Deutsche sind hier mit 22% vertreten. Die restlichen 18% verteilen sich auf 65 Nationalitäten. 

### 2. Herkunft nach Studienabschluss
Wer hat wo sein Arztstudium gemacht, und wurde der Facharzttitel in der Schweiz gemacht oder direkt anerkannt? 

Die Antworten auf diese Fragen haben eine höhere Aussagekraft als die Nationalität der registrierten Arztpersonen. Sie lassen bessere Rückschlüsse darauf zu, wieviele Ärzte ins Schweizer Gesundheitssystem immigriert sind. Dabei verwässern keine späteren Einbürgerungen die Zahlen, noch die Möglichkeit, dass in der Schweiz aufgewachsene ausländische Personen hier ihr Studium absolviert haben (aber Sprache und Kultur gut kennen). 

Diese Zahlen sollen detaillierter ausgewertet werden. Dabei geht es insbesondere auch darum, den Entwicklung über einzelnen Jahre zu erfassen. 

Zuerst schauen wir uns die Daten aller erfassten Psychiatrie-Spezialisten an:

In [87]:
df = pd.read_csv('medreg_2020_psych_b2019_20200126.csv')

## Problem entdeckt: einige Werte in der Spalte PP_Jahr haben den Wert 0!

Einige Daten wurden offenbar beim Parsing nicht richtig zugeordnet. Wir kontrollieren und korrigieren. 

In [109]:
df = pd.read_csv('medreg_2020_psych_20200125.csv')

In [114]:
df[df['PP_Jahr'] == 0]

Unnamed: 0  Doc_ID                                 Name Geschlecht  \
449          449    6610      Clerc, Marie-Thérèse Antoinette          w   
590          590    8784                   Masdea, Gianfranco          m   
1261        1261   18106                      Kuster, Daniela          w   
2610        2610   36426                      Gregori, Corina          w   
3927        3927   65577            Birnstiel, Anna Christina          w   
4237        4237   71632                   Starzer, Katharina          w   
4240        4240   71654  Käufling-Flesch, Christine Theresia          w   
4328        4328   72928      Mansfield, Friederike Franziska          w   
4956        4956   88438                Hilpert, Ralf Manfred          m   
5273        5273  101596            Andreew, Alexander Andrej          m   
5313        5313  103389         Kressin, Berndt Karl Wilhelm          m   

                                       Adresse                   Ort  \
449          Rue du Bugnon 46,1011 Lausanne,VD         1011 Lausanne   
590              L'Hôpital 140,1633 Marsens,FR          1633 Marsens   
1261                       ,9573 Littenheid,TG       9573 Littenheid   
2610           Bärenstutz 30,3110 Münsingen,BE        3110 Münsingen   
3927           Seftigenstrasse 41,3007 Bern,BE             3007 Bern   
4237             Rathausstrasse 1,6340 Baar,ZG             6340 Baar   
4240   Widenstrasse 55,6317 Oberwil bei Zug,ZG  6317 Oberwil bei Zug   
4328  Bahnhofstrasse 16+19,2502 Biel/Bienne,BE      2502 Biel/Bienne   
4956             Rathausstrasse 1,6341 Baar,ZG             6341 Baar   
5273   Widenstrasse 55,6317 Oberwil bei Zug,ZG  6317 Oberwil bei Zug   
5313   Widenstrasse 55,6317 Oberwil bei Zug,ZG  6317 Oberwil bei Zug   

           Nationalität       Sprache  Arzt_Jahr             Arzt_Land  \
449        Schweiz (CH)   Französisch       1995               Schweiz   
590        Schweiz (CH)   Französisch       1997               Schweiz   
1261       Schweiz (CH)       Deutsch       2003               Schweiz   
2610       Schweiz (CH)       Deutsch       1981               Schweiz   
3927       Schweiz (CH)       Deutsch       2007           Deutschland   
4237    Österreich (AT)       Deutsch       2004            Österreich   
4240   Deutschland (DE)       Deutsch       1983           Deutschland   
4328   Deutschland (DE)       Deutsch       2004           Deutschland   
4956   Deutschland (DE)       Deutsch       2002  Russische Föderation   
5273   Deutschland (DE)       Deutsch       2008           Deutschland   
5313   Deutschland (DE)                     1988           Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr PP_Land  PP_Anerkennung  \
449                     NaN        0     NaN             NaN   
590                     NaN        0     NaN             NaN   
1261                    NaN        0     NaN             NaN   
2610                    NaN        0     NaN             NaN   
3927                 2010.0        0     NaN             NaN   
4237                 2011.0        0     NaN             NaN   
4240                 2011.0        0     NaN             NaN   
4328                 2012.0        0     NaN             NaN   
4956                 2015.0        0     NaN             NaN   
5273                 2017.0        0     NaN             NaN   
5313                 2018.0        0     NaN             NaN   

                                                    BAB    BAB Status  \
449   Waadt                (2013), aktiv, MedBG, pri...  Kein Eintrag   
590   Freiburg                (2017), aktiv, MedBG, ...  Kein Eintrag   
1261  Thurgau                (2008), aktiv, Kt. Rech...       Erteilt   
2610  Bern                (1992), aktiv, MedBG, priv...       Erteilt   
3927  Bern                (2019), aktiv, MedBG, priv...       Erteilt   
4237  Zug                (2017), aktiv, MedBG, priva...       Erteilt   
4240  Zug                (2013), aktiv, MedBG, priva...    

Manuelle Nachkontrolle ergibt:
- Doc_ID 6610: PP korrekt, Wert wurde nicht übertragen, manuell nachgetragen (Zahnarzt und Arzt)
- Doc_ID 8784: PP korrekt, auch hier, Wert nicht übertragen (Arzt, Apotheker)
- Doc_ID 18106: falsch übernommen (Adresse Klinik für Psychiatrie und Psychotherapie Littenheid) - Datei gelöscht
- Doc_ID 36424: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 65577: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 71632: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 71654: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 72928: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 88438: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 101596: falsche Übernahme (auch wegen Adresse), gelöscht
- Doc_ID 103389: falsche Übernahme (auch wegen Adresse), gelöscht

In [118]:
df = pd.read_csv('medreg_2020_psych_b2019_20200126e.csv')

In [119]:
len(df)

5421

Wir mussten also insgesamt 9 Datensätze aus der Liste löschen. 

Das MedReg enthält Stand 26.1.2020 5431 Einträge für den Facharzt *Psychiatrie und Psychotherapie*. 

**Da wir bereits alle 2020er Werte ausgeschlossen haben, erscheint der Wert von 5421 als schlüssig.** Wir fahren mit der Datenanalyse weiter und wiederholen somit nicht den gesamten Parsing-Prozess.

In [141]:
df = pd.read_csv('medreg_2020_psych_b2019_20200126e.csv')

In [121]:
df['Arzt_Land'].value_counts()

Schweiz                      2835
Deutschland                  1357
Frankreich                    317
Italien                       214
Österreich                    179
Spanien                        73
Rumänien                       61
Griechenland                   58
vorm. Jugoslawien              42
Belgien                        41
Bulgarien                      21
Polen                          21
Algerien                       19
Ungarn                         17
vorm. Sowjetunion              14
Russische Föderation           13
Niederlande                    12
Portugal                       10
Slowakei                        8
Serbien Republik                8
Grossbritannien                 8
Peru                            7
Brasilien                       6
Argentinien                     6
Kroatien                        5
Tschechische Republik           5
Ägypten                         4
Ukraine                         4
Slowenien                       4
Mexiko        

In [122]:
len(df)

5421

In [123]:
df_arzt_land = df['Arzt_Land'].value_counts()

In [124]:
df_arzt_land = df_arzt_land.reset_index()

In [125]:
df_arzt_land.head(3)

index  Arzt_Land
0      Schweiz       2835
1  Deutschland       1357
2   Frankreich        317

In [126]:
df_arzt_land = df_arzt_land.rename(columns = {'index':'Land Medizinstudium', 'Arzt_Land':'Anzahl'})

In [127]:
df_arzt_land['Anteil'] = df_arzt_land['Anzahl'] / 5430 * 100

In [1]:
df_arzt_land.to_csv(r'Psych_Land_Medizinstudium_bis2019.csv',index = 'Land Medizinstudium', header=True)

NameError: name 'df_arzt_land' is not defined

In [129]:
df_arzt_land.head(5)

Land Medizinstudium  Anzahl     Anteil
0             Schweiz    2835  52.209945
1         Deutschland    1357  24.990792
2          Frankreich     317   5.837937
3             Italien     214   3.941068
4          Österreich     179   3.296501

### Resultat 3: die Hälfte hat in der Schweiz Medizin studiert, die andere Hälfte im Ausland - die meisten davon in Deutschland
Also noch bei etwa der Hälfte aller registrierten Facharzttitel wurde auch das Grundstudium in der Schweiz gemacht. 
Doch wie sah es über die letzten 10 Jahren aus?

Das wird nun etwas komplizierter bei der Auswertung. 
Wenn das Land des Weiterbildungstitels die Schweiz ist, zählt der Wert in PP_Jahr. Wenn das WBT-Land nicht die Schweiz ist, ist die Anerkennung des Facharzttitels (PP_Anerkennung) massgeblich. Bringe ich das in eine einfache Formel?

Wir versuchen es, die Werte aus den Zulassungen in der Schweiz (PP_Jahr) und jene, die direkt anerkannt wurden, in eine neue Spalte PP_CH zu überführen. Am einfachsten wäre es doch, sämtliche Jahreswerte aus PP_Jahr in die Kolonne zu übertragen und dann mit den zusätzlichen Werten von PP_Anerkennung zu überschreiben. 

In [148]:
df['PP_CH'] = df['PP_Jahr']

In [149]:
df.head(5)

Unnamed: 0  Doc_ID                     Name Geschlecht  \
0           0     552       Poleski, Alexander          m   
1           1     566       Langegger, Florian          m   
2           2     590      Rivera Prada, Jaime          m   
3           3     611         Dentoni, Roberto          m   
4           4     617  Anastopoulos, Anastasio          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   
3             via Simen 10,6900 Lugano,TI    6900 Lugano   Schweiz (CH)   
4                            Kein Eintrag            NaN   Schweiz (CH)   

                     Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  \
0                Französisch       1985   Schweiz                    NaN   
1                    Deutsch       1985   Schweiz                    NaN   
2                Französisch       1985   Schweiz                    NaN   
3   Französisch, Italienisch       1986   Schweiz                    NaN   
4                Französisch       1986   Schweiz                    NaN   

   PP_Jahr  PP_Land  PP_Anerkennung  \
0     1986  Schweiz             NaN   
1     1985  Schweiz             NaN   
2     1987  Schweiz             NaN   
3     1991  Schweiz             NaN   
4     1986  Schweiz             NaN   

                                                 BAB BAB Status  \
0  Waadt                (1986), aktiv, MedBG, pri...    Erteilt   
1  Thurgau                (2017), aktiv, MedBG, p...    Erteilt   
2   Wallis                (2014), inaktiv, Unbekannt    Erteilt   
3  Tessin                (1997), aktiv, MedBG, pr...    Erteilt   
4  Waadt                (2017), inaktiv, MedBG, p...    Erteilt   

             Datei  PP_CH  
0  medreg_552.html   1986  
1  medreg_566.html   1985  
2  medreg_590.html   1987  
3  medreg_611.html   1991  
4  medreg_617.html   1986

In [150]:
df['PP_CH'] = df['PP_Anerkennung']

In [151]:
df

Unnamed: 0  Doc_ID                                               Name  \
0              0     552                                 Poleski, Alexander   
1              1     566                                 Langegger, Florian   
2              2     590                                Rivera Prada, Jaime   
3              3     611                                   Dentoni, Roberto   
4              4     617                            Anastopoulos, Anastasio   
5              5     709                                       Cotar, Boris   
6              6     712                                     Lierow, Konrad   
7              7     726                                    Borens, Raymond   
8              8     735                      Guignard-Luz, Inma-Concepcion   
9              9     736                            Ioset-Lanoy, Anne-Marie   
10            10     737                                   Salvador, Arturo   
11            11     744                                 Rezzonico, Giorgio   
12            12     752                                      Vahdat, Abbas   
13            13     761                                  Arneberg, Oernulf   
14            14     765                                     Gerlach, Willi   
15            15     768                                Ryffel-Rawak, Doris   
16            16     769                                      Schöpf, Josef   
17            17     776                                  Genta, Maggiorino   
18            18     777                             Harel, Marek Mordechai   
19            19     784                   Kiesewetter, Arno Martin Wilhelm   
20            20     903                              Barz, Andreas Florian   
21            21     913                            Dreifuss, Markus Kilian   
22            22     914                   D'Souza, Christine Kamala Sophia   
23            23     956                           Pletscher, Markus Walter   
24            24     973                           Steiner, Franziska Beate   
25            25     992                                      Rost, Barbara   
26            26    1028                                       Hüsler, Jürg   
27            27    1029                                       Imbach, René   
28            28    1030                       Isenschmid, Bettina Marianne   
29            29    1048                              Minder, Bernard André   
30            30    1071                             Schüpbach, Daniel Hans   
31            31    1090                     Bartholdi von Rotz, Sarah Ruth   
32            32    1092                                  Bernasconi, Mauro   
33            33    1096                                    Bohnhoff, Zsolt   
34            34    1100                                 Bridler, René Milo   
35            35    1129                           Hirsbrunner, Stephan Urs   
36            36    1152                    Mekler-Kessler, Gabriele Andrea   
37            37    1156                                      Noser, Othmar   
38            38    1168                          Rüttner Götzmann, Barbara   
39            39    1199                                    Quadri, Antonio   
40            40    1202                                   Sobhani, Hossein   
41            41    1205                                    Vianello, Mario   
42            42    1208                                   Döhmann, Michael   
43            43    1212                                   Kötscher, Dagmar   
44            44    1219                            Borella, Glayds Eugenia   
45            45    1220                                 Fortini, Krzysztof   
46            46    1221                             Joliat-Duberg, Suzanna   
47            47    1222                  Schteingart Gitnacht, Alicia Sara   
48            48    1223                        Vasiliu-Georgescu, Nathalie   
49            49    1226                              Ho

Überschreibt leider alle Werte. 

Könnte es mit einer OR-Bedingung besser klappen? Entweder alle mit einem Wert in PP_Anerkennung und sonst jene aus PP_Jahr.

In [159]:
df['PP_Anerkennung'] = df['PP_Anerkennung'].astype('int')

ValueError: Cannot convert non-finite values (NA or inf) to integer

In [156]:
df['PP_CH'] = df[~(pd.isnull(df['PP_Anerkennung'])) | (df['PP_Jahr'])]

In [157]:
df.head(5)

Unnamed: 0  Doc_ID                     Name Geschlecht  \
0           0     552       Poleski, Alexander          m   
1           1     566       Langegger, Florian          m   
2           2     590      Rivera Prada, Jaime          m   
3           3     611         Dentoni, Roberto          m   
4           4     617  Anastopoulos, Anastasio          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   
3             via Simen 10,6900 Lugano,TI    6900 Lugano   Schweiz (CH)   
4                            Kein Eintrag            NaN   Schweiz (CH)   

                     Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  \
0                Französisch       1985   Schweiz                    NaN   
1                    Deutsch       1985   Schweiz                    NaN   
2                Französisch       1985   Schweiz                    NaN   
3   Französisch, Italienisch       1986   Schweiz                    NaN   
4                Französisch       1986   Schweiz                    NaN   

   PP_Jahr  PP_Land  PP_Anerkennung  \
0     1986  Schweiz             NaN   
1     1985  Schweiz             NaN   
2     1987  Schweiz             NaN   
3     1991  Schweiz             NaN   
4     1986  Schweiz             NaN   

                                                 BAB BAB Status  \
0  Waadt                (1986), aktiv, MedBG, pri...    Erteilt   
1  Thurgau                (2017), aktiv, MedBG, p...    Erteilt   
2   Wallis                (2014), inaktiv, Unbekannt    Erteilt   
3  Tessin                (1997), aktiv, MedBG, pr...    Erteilt   
4  Waadt                (2017), inaktiv, MedBG, p...    Erteilt   

             Datei PP_CH  
0  medreg_552.html     0  
1  medreg_566.html     1  
2  medreg_590.html     2  
3  medreg_611.html     3  
4  medreg_617.html     4

Macht eine Art Index. Wieso es hochzählt? Keine Ahnung. Wir versuchen noch die NaN auf 0 zu setzen. 

In [162]:
df['PP_Anerkennung'] = df['PP_Anerkennung'].fillna(0)

In [163]:
df['PP_Anerkennung'] = df['PP_Anerkennung'].astype('int')

In [164]:
df.dtypes

Unnamed: 0                 int64
Doc_ID                     int64
Name                      object
Geschlecht                object
Adresse                   object
Ort                       object
Nationalität              object
Sprache                   object
Arzt_Jahr                  int64
Arzt_Land                 object
Arzt_Anerkennung_Jahr    float64
PP_Jahr                    int64
PP_Land                   object
PP_Anerkennung             int64
BAB                       object
BAB Status                object
Datei                     object
PP_CH                     object
dtype: object

In [ ]:
df = df.drop(['Unnamed: 0'],axis=1)

In [168]:
df = df.drop(['PP_CH'],axis=1)

In [171]:
df['PP_CH'] = df[(df['PP_Anerkennung']>['PP_Jahr']) | (df['PP_Jahr'])]

ValueError: Lengths must match to compare

In [172]:
df.head(5)

Doc_ID                     Name Geschlecht  \
0     552       Poleski, Alexander          m   
1     566       Langegger, Florian          m   
2     590      Rivera Prada, Jaime          m   
3     611         Dentoni, Roberto          m   
4     617  Anastopoulos, Anastasio          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   
3             via Simen 10,6900 Lugano,TI    6900 Lugano   Schweiz (CH)   
4                            Kein Eintrag            NaN   Schweiz (CH)   

                     Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  \
0                Französisch       1985   Schweiz                    NaN   
1                    Deutsch       1985   Schweiz                    NaN   
2                Französisch       1985   Schweiz                    NaN   
3   Französisch, Italienisch       1986   Schweiz                    NaN   
4                Französisch       1986   Schweiz                    NaN   

   PP_Jahr  PP_Land  PP_Anerkennung  \
0     1986  Schweiz               0   
1     1985  Schweiz               0   
2     1987  Schweiz               0   
3     1991  Schweiz               0   
4     1986  Schweiz               0   

                                                 BAB BAB Status  \
0  Waadt                (1986), aktiv, MedBG, pri...    Erteilt   
1  Thurgau                (2017), aktiv, MedBG, p...    Erteilt   
2   Wallis                (2014), inaktiv, Unbekannt    Erteilt   
3  Tessin                (1997), aktiv, MedBG, pr...    Erteilt   
4  Waadt                (2017), inaktiv, MedBG, p...    Erteilt   

             Datei  
0  medreg_552.html  
1  medreg_566.html  
2  medreg_590.html  
3  medreg_611.html  
4  medreg_617.html

Wir wollen es mit einer definierten Funktion und mit *lambda* versuchen:

In [179]:
def combine(ausland,ch):
    if 'PP_Anerkennung' > 0 in ausland:
        return ausland
    else: 
        return ch

df['PP_CH'] = df.apply(lambda x: combine(x['PP_Anerkennung'],x['PP_Jahr'], axis=1))

KeyError: ('PP_Anerkennung', 'occurred at index Doc_ID')

Nochmals, dieses Mal ohne Funktion, sondern bloss mit einer Variable für die Werte und eine nette, logische Formel:

In [213]:
df['PP_CH'] = df.apply(lambda x: (x['PP_Anerkennung'] if ['PP_Anerkennung'] > ['PP_Jahr'] else x['PP_Jahr']), axis=1)

In [214]:
df.tail(5)

Doc_ID                        Name Geschlecht       Adresse  Ort  \
5416  113298      Sehim-Bensaber, Nacéra          w  Kein Eintrag  NaN   
5417  113305                Abadie, Hadi          m  Kein Eintrag  NaN   
5418  113427     Armion, Roxana Georgeta          w  Kein Eintrag  NaN   
5419  113540     Manouelian, Edmond Jean          m  Kein Eintrag  NaN   
5420  113646  Mühlhauser, Markus Gerhard          m  Kein Eintrag  NaN   

           Nationalität       Sprache  Arzt_Jahr    Arzt_Land  \
5416       Schweiz (CH)   Französisch       2019      Schweiz   
5417    Frankreich (FR)                     2014   Frankreich   
5418   Deutschland (DE)       Deutsch       2004  Deutschland   
5419    Frankreich (FR)                     1992   Frankreich   
5420   Deutschland (DE)                     1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

               BAB    BAB Status               Datei  PP_CH  
5416  Kein Eintrag  Kein Eintrag  medreg_113298.html   2019  
5417  Kein Eintrag  Kein Eintrag  medreg_113305.html   2014  
5418  Kein Eintrag  Kein Eintrag  medreg_113427.html   2012  
5419  Kein Eintrag  Kein Eintrag  medreg_113540.html   1992  
5420  Kein Eintrag  Kein Eintrag  medreg_113646.html   2014

Fast geschafft! Nach mindestens 2 Stunden rumpröbeln und suchen. Noch ist ein Fehler in der Logik der Formel, den ich nicht nachvollziehen kann. Der Teil *['PP_Anerkennung'] > ['PP_Jahr']* funktioniert nicht korrekt. Wir versuchen es noch so:

In [191]:
df["PP_CH"] = df.apply(lambda x: (x['PP_Jahr'] if ['PP_Land'] == 'Schweiz' else x["PP_Anerkennung"]), axis=1)

In [192]:
df.tail(5)

Doc_ID                        Name Geschlecht       Adresse  Ort  \
5416  113298      Sehim-Bensaber, Nacéra          w  Kein Eintrag  NaN   
5417  113305                Abadie, Hadi          m  Kein Eintrag  NaN   
5418  113427     Armion, Roxana Georgeta          w  Kein Eintrag  NaN   
5419  113540     Manouelian, Edmond Jean          m  Kein Eintrag  NaN   
5420  113646  Mühlhauser, Markus Gerhard          m  Kein Eintrag  NaN   

           Nationalität       Sprache  Arzt_Jahr    Arzt_Land  \
5416       Schweiz (CH)   Französisch       2019      Schweiz   
5417    Frankreich (FR)                     2014   Frankreich   
5418   Deutschland (DE)       Deutsch       2004  Deutschland   
5419    Frankreich (FR)                     1992   Frankreich   
5420   Deutschland (DE)                     1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

               BAB    BAB Status               Datei  PP_CH  
5416  Kein Eintrag  Kein Eintrag  medreg_113298.html      0  
5417  Kein Eintrag  Kein Eintrag  medreg_113305.html   2019  
5418  Kein Eintrag  Kein Eintrag  medreg_113427.html   2019  
5419  Kein Eintrag  Kein Eintrag  medreg_113540.html   2019  
5420  Kein Eintrag  Kein Eintrag  medreg_113646.html   2019

Geht auch nicht. Irgendwie rechnet es die Zeilen in der falschen Reihendfolge durch. Nochmals simpel:

In [197]:
df["PP_CH"] = df.apply(lambda x: (x["PP_Jahr"] if ["PP_Anerkennung"] == 0 else x['PP_Anerkennung']), axis=1)

In [198]:
df.tail(5)

Doc_ID                        Name Geschlecht       Adresse  Ort  \
5416  113298      Sehim-Bensaber, Nacéra          w  Kein Eintrag  NaN   
5417  113305                Abadie, Hadi          m  Kein Eintrag  NaN   
5418  113427     Armion, Roxana Georgeta          w  Kein Eintrag  NaN   
5419  113540     Manouelian, Edmond Jean          m  Kein Eintrag  NaN   
5420  113646  Mühlhauser, Markus Gerhard          m  Kein Eintrag  NaN   

           Nationalität       Sprache  Arzt_Jahr    Arzt_Land  \
5416       Schweiz (CH)   Französisch       2019      Schweiz   
5417    Frankreich (FR)                     2014   Frankreich   
5418   Deutschland (DE)       Deutsch       2004  Deutschland   
5419    Frankreich (FR)                     1992   Frankreich   
5420   Deutschland (DE)                     1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

               BAB    BAB Status               Datei  PP_CH  
5416  Kein Eintrag  Kein Eintrag  medreg_113298.html      0  
5417  Kein Eintrag  Kein Eintrag  medreg_113305.html   2019  
5418  Kein Eintrag  Kein Eintrag  medreg_113427.html   2019  
5419  Kein Eintrag  Kein Eintrag  medreg_113540.html   2019  
5420  Kein Eintrag  Kein Eintrag  medreg_113646.html   2019

In [211]:
df["PP_CH"] = df.apply(lambda x: (x['PP_Anerkennung'] if ['PP_Anerkennung'] != 0 else x["PP_Jahr"]), axis=1)

In [212]:
df.tail(5)

Doc_ID                        Name Geschlecht       Adresse  Ort  \
5416  113298      Sehim-Bensaber, Nacéra          w  Kein Eintrag  NaN   
5417  113305                Abadie, Hadi          m  Kein Eintrag  NaN   
5418  113427     Armion, Roxana Georgeta          w  Kein Eintrag  NaN   
5419  113540     Manouelian, Edmond Jean          m  Kein Eintrag  NaN   
5420  113646  Mühlhauser, Markus Gerhard          m  Kein Eintrag  NaN   

           Nationalität       Sprache  Arzt_Jahr    Arzt_Land  \
5416       Schweiz (CH)   Französisch       2019      Schweiz   
5417    Frankreich (FR)                     2014   Frankreich   
5418   Deutschland (DE)       Deutsch       2004  Deutschland   
5419    Frankreich (FR)                     1992   Frankreich   
5420   Deutschland (DE)                     1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

               BAB    BAB Status               Datei  PP_CH  
5416  Kein Eintrag  Kein Eintrag  medreg_113298.html      0  
5417  Kein Eintrag  Kein Eintrag  medreg_113305.html   2019  
5418  Kein Eintrag  Kein Eintrag  medreg_113427.html   2019  
5419  Kein Eintrag  Kein Eintrag  medreg_113540.html   2019  
5420  Kein Eintrag  Kein Eintrag  medreg_113646.html   2019

In [224]:
df['PP_CH'] = df.apply(lambda x: (x["PP_Jahr"] if x["PP_Anerkennung"] == 0 else x['PP_Anerkennung']), axis=1)

In [225]:
df.tail(5)

Doc_ID                        Name Geschlecht       Adresse  Ort  \
5416  113298      Sehim-Bensaber, Nacéra          w  Kein Eintrag  NaN   
5417  113305                Abadie, Hadi          m  Kein Eintrag  NaN   
5418  113427     Armion, Roxana Georgeta          w  Kein Eintrag  NaN   
5419  113540     Manouelian, Edmond Jean          m  Kein Eintrag  NaN   
5420  113646  Mühlhauser, Markus Gerhard          m  Kein Eintrag  NaN   

           Nationalität       Sprache  Arzt_Jahr    Arzt_Land  \
5416       Schweiz (CH)   Französisch       2019      Schweiz   
5417    Frankreich (FR)                     2014   Frankreich   
5418   Deutschland (DE)       Deutsch       2004  Deutschland   
5419    Frankreich (FR)                     1992   Frankreich   
5420   Deutschland (DE)                     1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

               BAB    BAB Status               Datei  PP_CH  
5416  Kein Eintrag  Kein Eintrag  medreg_113298.html   2019  
5417  Kein Eintrag  Kein Eintrag  medreg_113305.html   2019  
5418  Kein Eintrag  Kein Eintrag  medreg_113427.html   2019  
5419  Kein Eintrag  Kein Eintrag  medreg_113540.html   2019  
5420  Kein Eintrag  Kein Eintrag  medreg_113646.html   2019

In [226]:
df.head(5)

Doc_ID                     Name Geschlecht  \
0     552       Poleski, Alexander          m   
1     566       Langegger, Florian          m   
2     590      Rivera Prada, Jaime          m   
3     611         Dentoni, Roberto          m   
4     617  Anastopoulos, Anastasio          m   

                                  Adresse            Ort   Nationalität  \
0  Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   Schweiz (CH)   
1            Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   Schweiz (CH)   
2                            Kein Eintrag            NaN   Schweiz (CH)   
3             via Simen 10,6900 Lugano,TI    6900 Lugano   Schweiz (CH)   
4                            Kein Eintrag            NaN   Schweiz (CH)   

                     Sprache  Arzt_Jahr Arzt_Land  Arzt_Anerkennung_Jahr  \
0                Französisch       1985   Schweiz                    NaN   
1                    Deutsch       1985   Schweiz                    NaN   
2                Französisch       1985   Schweiz                    NaN   
3   Französisch, Italienisch       1986   Schweiz                    NaN   
4                Französisch       1986   Schweiz                    NaN   

   PP_Jahr  PP_Land  PP_Anerkennung  \
0     1986  Schweiz               0   
1     1985  Schweiz               0   
2     1987  Schweiz               0   
3     1991  Schweiz               0   
4     1986  Schweiz               0   

                                                 BAB BAB Status  \
0  Waadt                (1986), aktiv, MedBG, pri...    Erteilt   
1  Thurgau                (2017), aktiv, MedBG, p...    Erteilt   
2   Wallis                (2014), inaktiv, Unbekannt    Erteilt   
3  Tessin                (1997), aktiv, MedBG, pr...    Erteilt   
4  Waadt                (2017), inaktiv, MedBG, p...    Erteilt   

             Datei  PP_CH  
0  medreg_552.html   1986  
1  medreg_566.html   1985  
2  medreg_590.html   1987  
3  medreg_611.html   1991  
4  medreg_617.html   1986

### Endlich!
Drei Stunden vorbei mit rumdoktern. Und es war nur ein x zuwenig.

Vor jede Spalte gehört ein x, damit der Wert verwendet wird. So würden wohl all die oben ausporpierten Formeln funktionieren. Oje.


Zuerst abspeichern.

In [227]:
df.to_csv(r'medreg_2020_psych_b2019_20200127.csv',index = True, header = True)

# Attention please. Weiterer Fehler entdeckt
Bei der Kontrolle der Daten wurden eine weiterer Eintrag mit dem Anerkennungsdatum 2020 gefunden. Leider gingen beim Ausschliessen der 2020er-Daten die Schweizer Abschlüsse vergessen. Deshalb wird der akutellste Datensatz jetzt nochmals überprüft:

In [10]:
df = pd.read_csv(r'medreg_2020_psych_b2019_20200127.csv')

In [6]:
df[df['PP_Jahr']>2019]

Unnamed: 0  Doc_ID                              Name Geschlecht  \
1854        1854   27363           FRANZ, Tatjana Stefanie          w   
3775        3775   60313     Mpairaktaridou Berger, Salome          w   
3952        3952   65718             Weyand, Thomas Martin          m   
4448        4448   75346                   Vibert, Vincent          m   
4589        4589   78316                Tsilikas, Nikolaos          m   
4700        4700   81452  Patru ép. Beroud, Maria Cristina          w   
4827        4827   84083                    Selle, Valerio          m   
5128        5128   94643        Schild, Sebastian Benjamin          m   

                                       Adresse          Ort  \
1854                              Kein Eintrag          NaN   
3775             Chamerstrasse 12a,6300 Zug,ZG     6300 Zug   
3952                              Kein Eintrag          NaN   
4448                              Kein Eintrag          NaN   
4589                              Kein Eintrag          NaN   
4700  Rue   Micheli-Du-Crest 24,1205 Genève,GE  1205 Genève   
4827                              Kein Eintrag          NaN   
5128                              Kein Eintrag          NaN   

            Nationalität       Sprache  Arzt_Jahr     Arzt_Land  \
1854        Schweiz (CH)   Französisch       2007       Schweiz   
3775   Griechenland (GR)       Deutsch       1990   Deutschland   
3952    Deutschland (DE)       Deutsch       2005   Deutschland   
4448        Schweiz (CH)   Französisch       2012       Schweiz   
4589   Griechenland (GR)   Französisch       2006  Griechenland   
4700     Frankreich (FR)   Französisch       2003    Frankreich   
4827        Italien (IT)   Italienisch       2010       Italien   
5128    Deutschland (DE)       Deutsch       2011   Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr  PP_Land  PP_Anerkennung  \
1854                    NaN     2020  Schweiz               0   
3775                 2009.0     2020  Schweiz               0   
3952                 2010.0     2020  Schweiz               0   
4448                    NaN     2020  Schweiz               0   
4589                 2013.0     2020  Schweiz               0   
4700                 2014.0     2020  Schweiz               0   
4827                 2014.0     2020  Schweiz               0   
5128                 2016.0     2020  Schweiz               0   

                                                    BAB    BAB Status  \
1854                                       Kein Eintrag  Kein Eintrag   
3775  Zug                (2010), aktiv, MedBG, priva...       Erteilt   
3952                                       Kein Eintrag  Kein Eintrag   
4448       Genf                (2013), aktiv, Unbekannt       Erteilt   
4589                                       Kein Eintrag  Kein Eintrag   
4700  Genf                (2014), aktiv, MedBG, priv...       Erteilt   
4827                                       Kein Eintrag  Kein Eintrag   
5128                                       Kein Eintrag  Kein Eintrag   

                  Datei  PP_CH  
1854  medreg_27363.html   2020  
3775  medreg_60313.html   2020  
3952  medreg_65718.html   2020  
4448  medreg_75346.html   2020  
4589  medreg_78316.html   2020  
4700  medreg_81452.html   2020  
4827  medreg_84083.html   2020  
5128  medreg_94643.html   2020

Wir haben also 9 Einträge, die noch aus der Datenbank entfernt werden müssen. 

In [7]:
len(df)

5421

In [11]:
df = df[df['PP_Jahr']<2020]

In [12]:
len(df)

5413

Wieso eigentlich wird den Dataframes ständig eine neue Kolonne «Unnamed: 0» hinzugefügt?

In [15]:
df.drop('Unnamed: 0', axis=1)

Doc_ID                        Name Geschlecht  \
0        552          Poleski, Alexander          m   
1        566          Langegger, Florian          m   
2        590         Rivera Prada, Jaime          m   
3        611            Dentoni, Roberto          m   
4        617     Anastopoulos, Anastasio          m   
...      ...                         ...        ...   
5416  113298      Sehim-Bensaber, Nacéra          w   
5417  113305                Abadie, Hadi          m   
5418  113427     Armion, Roxana Georgeta          w   
5419  113540     Manouelian, Edmond Jean          m   
5420  113646  Mühlhauser, Markus Gerhard          m   

                                     Adresse            Ort  \
0     Chemin des Allières 1,1012 Lausanne,VD  1012 Lausanne   
1               Seestrasse 22,8592 Uttwil,TG    8592 Uttwil   
2                               Kein Eintrag            NaN   
3                via Simen 10,6900 Lugano,TI    6900 Lugano   
4                               Kein Eintrag            NaN   
...                                      ...            ...   
5416                            Kein Eintrag            NaN   
5417                            Kein Eintrag            NaN   
5418                            Kein Eintrag            NaN   
5419                            Kein Eintrag            NaN   
5420                            Kein Eintrag            NaN   

           Nationalität                    Sprache  Arzt_Jahr    Arzt_Land  \
0          Schweiz (CH)                Französisch       1985      Schweiz   
1          Schweiz (CH)                    Deutsch       1985      Schweiz   
2          Schweiz (CH)                Französisch       1985      Schweiz   
3          Schweiz (CH)   Französisch, Italienisch       1986      Schweiz   
4          Schweiz (CH)                Französisch       1986      Schweiz   
...                 ...                        ...        ...          ...   
5416       Schweiz (CH)                Französisch       2019      Schweiz   
5417    Frankreich (FR)                                  2014   Frankreich   
5418   Deutschland (DE)                    Deutsch       2004  Deutschland   
5419    Frankreich (FR)                                  1992   Frankreich   
5420   Deutschland (DE)                                  1999  Deutschland   

      Arzt_Anerkennung_Jahr  PP_Jahr      PP_Land  PP_Anerkennung  \
0                       NaN     1986      Schweiz               0   
1                       NaN     1985      Schweiz               0   
2                       NaN     1987      Schweiz               0   
3                       NaN     1991      Schweiz               0   
4                       NaN     1986      Schweiz               0   
...                     ...      ...          ...             ...   
5416                    NaN     2019      Schweiz               0   
5417                 2019.0     2014   Frankreich            2019   
5418                 2019.0     2012  Deutschland            2019   
5419                 2019.0     1992   Frankreich            2019   
5420                 2019.0     2014  Deutschland            2019   

                                                    BAB    BAB Status  \
0     Waadt                (1986), aktiv, MedBG, pri...       Erteilt   
1     Thurgau                (2017), aktiv, MedBG, p...       Erteilt   
2      Wallis                (2014), inaktiv, Unbekannt       Erteilt   
3     Tessin                (1997), aktiv, MedBG, pr...       Erteilt   
4     Waadt                (2017), inaktiv, MedBG, p...       Erteilt   
...                                                 ...           ...   
5416                                       Kein Eintrag  Kein Eintrag   
5417                                       Kein Eintrag  Kein Eintrag   
5418                                       Kein Eintrag  Kein Eintrag   
5419                                       Kein Eintrag  Kein Eintrag   
5420               

In [16]:
df.to_csv(r'medreg_2020_psych_b2019_20200128.csv',index = True, header = True)

Jetzt wollen wir die Daten nochmals auf die Korrektheit überprüfen. Die Referenz ist für uns dabei die Excel-Datei des BAG «rohdaten-aktive-bab-med-2018_mod.xlsx».

In [diesem Notebook](/Users/master/Desktop/CAS_DJ/MedReg/Daten_BAG/MedReg_Check_rohdaten-aktive-bab-med-2018_mod.ipynb) wurden die Daten entsprechend ausgewertet. So ergab die Analyse dort 4337 Psychiater mit erteilter BAB. 

In [1]:
import pandas as pd
import numpy as np
import re

In [2]:
df = pd.read_csv(r'medreg_2020_psych_b2019_20200128.csv')

In [3]:
df_erteilt = df[df['BAB Status'] == 'Erteilt']

In [4]:
len(df_erteilt)

4415

In [5]:
df_erteilt_2018 = df_erteilt[df_erteilt['PP_CH'] < 2019]

In [6]:
len(df_erteilt_2018)

4344

Wir kommen dabei auf 4344 Einträge. Das sind 7 mehr als in der Excel-Datei das BAG von 2018. Haben wir nach wie vor einige Irrläufer in unseren gescrapten Daten? Wie sieht der Unterschied im Jahr 2018 aus? 

In [7]:
df_erteilt_2018['Arzt_Land'].value_counts()

Schweiz                      2526
Deutschland                   973
Frankreich                    192
Italien                       147
Österreich                    133
Spanien                        55
Rumänien                       45
vorm. Jugoslawien              41
Griechenland                   39
Belgien                        31
Bulgarien                      13
Polen                          13
Ungarn                         12
Algerien                       11
Niederlande                     8
Portugal                        7
vorm. Sowjetunion               7
Peru                            6
Brasilien                       6
Slowakei                        6
Tschechische Republik           5
Russische Föderation            5
Serbien Republik                5
Grossbritannien                 4
Kroatien                        4
Argentinien                     4
Mexiko                          3
Kuba                            3
Bosnien und Herzegowina         2
Tunesien      

Unsere Scrapingdaten zeigen bis 2018:
Schweiz                      2526
Deutschland                   973
Frankreich                    192
Italien                       147

Die Excel-Tabelle des BAG von 2018 zeigt:
Schweiz                      2497
Deutschland                   999
Frankreich                    182
Italien                       152



Ist diese Fluktuation normal? Wir nehmen noch die vom BAG bereitgestellten Daten aus dem Jahre 2017 hinzu und vergleichen sie mit dem Datensatz von 2018 ([Notebook](/Users/master/Desktop/CAS_DJ/MedReg/Daten_BAG/MedReg_Check_rohdaten-aktive-bab-med-2018_mod.ipynb)), wo nur Entscheide bis 2017 berücksichtigt werden. 


In [11]:
df2019_b2017 = df_erteilt_2018[df_erteilt_2018['PP_CH'] < 2017]

In [12]:
len(df2019_b2017)

4044

Achtung Update 31.1.2020: dummer Fehler, wir haben damit auch die Werte von 2017 ausgeschlossen!


In [13]:
df2019_b2017 = df_erteilt_2018[df_erteilt_2018['PP_CH'] < 2018]

In [14]:
len(df2019_b2017)

4208

In [15]:
df2019_b2017['Arzt_Land'].value_counts()

Schweiz                      2490
Deutschland                   931
Frankreich                    176
Italien                       137
Österreich                    129
Spanien                        54
vorm. Jugoslawien              41
Rumänien                       38
Griechenland                   34
Belgien                        30
Polen                          11
Bulgarien                      11
Ungarn                         10
Algerien                        9
Niederlande                     8
Portugal                        7
Slowakei                        6
vorm. Sowjetunion               6
Brasilien                       6
Peru                            6
Tschechische Republik           5
Russische Föderation            5
Kroatien                        4
Argentinien                     4
Serbien Republik                4
Mexiko                          3
Kuba                            3
Grossbritannien                 3
Syrien arabische Republik       2
Slowenien     

Die Excel-Tabelle des BAG von 2017 ergibt:
Total: 4212

ErteilungslandDiplom
Schweiz 2522
Deutschland 939
Frankreich 156
Italien 140


Die Excel-Tabelle des BAG von 2018 ergibt bis 2017 (JahrEntscheidBewilligung):
Total: 3804

ErteilungslandDiplom
Schweiz                      2340
Deutschland                   841
Italien                       122
Frankreich                    114

Update 31.1.2020: ich habe die Zahlen von 2018 falsch berechnet. Siehe [Notebook](/Users/master/Desktop/CAS_DJ/MedReg/Daten_BAG/MedReg_Check_rohdaten-aktive-bab-med-2018_mod.ipynb).
Total 4073

Schweiz                      2414
Deutschland                   921
Frankreich                    147
Italien                       139


Die Daten des Scraping, eingegrenzt auf die Bewilligungen bis 2017 (PP_CH) ergeben:
Total: 4044
Schweiz                      2453
Deutschland                   888
Frankreich                    144
Italien                       129

Update 31.1.2020: ich habe die Zahlen von 2018 falsch berechnet. Wir erhalten nun:
Total: 4208
Schweiz                      2490
Deutschland                   931
Frankreich                    176
Italien                       137


Erstes Fazit: Auffällig ist besonders die grosse Veränderung der Datensätze 2017 bis 2018 des BAG. Für eine Erklärung haben wir das BAG per Email angefragt (29.1.2020). Die Schwankungen werden so begründet: «Die Einträge zu den Berufsausübungsbewilligungen werden von den kantonalen Behörden im MedReg vorgenommen. Abweichungen können entstehen, wenn nachträglich Mutationen vorgenommen werden.»

Die Zahlen der gescrapten Daten von 2019 liegen im Schwankungsbereich der vom BAG zur Verfügung gestellten Datensätze. Sie sind mit den Mutationen durch die Kantone zu erklären. Zudem stimmt das Total der gefundenen Facharzttitel nahezu mit dem aktuellsten Stand der (stäntig aktualisierten) Datenbank überein.

Die Anlayse der Daten soll mit dem bereinigten Datensatz im Notebook MedReg_Analyse_03 nochmals wiederholt werden. 

Zudem werden wir für diese Analysen weiterhin die Daten **aller** registrierten Arzttitel verwenden und nicht bloss jene mit erteilten Bewilligungen, da diese nur für eine bestimmte Art von (selbstständigen) Tätigkeiten nötig ist. So schrieb das BAG auf eine Anfrage im letzten Herbst: *«Die Statistiken des BAG zu den aktiven Bewilligungen nach MedBG 2018 resultieren aus den von den Kantonen erteilten Berufsausübungsbewilligungen. Eine solche Bewilligung ist aufgrund des Medizinalberufegesetzes (MedBG) für die privatwirtschaftliche Berufsausübung in eigener fachlicher Verantwortung notwendig. Es sind somit nicht alle Tätigkeiten bewilligungspflichtig. Entsprechend kann das BAG keine Aussagen dazu machen, wie viele Ärzt/innen in der Schweiz ihren Beruf tatsächlich ausüben.»*


 